In [511]:
import pandas as pd													# data manipulation
import matplotlib.pyplot as plt												# graphs
import seaborn as sns													# graphs
import numpy as np													# graphs
from scipy.stats import norm												# statistics
from sklearn.preprocessing import StandardScaler									# statistics
from scipy import stats													# statistics
from math import *													# advance calculation	
import math as math
import statistics
from matplotlib import cm												# graphs
import sys														# system functions
import warnings														# indicating warnings
warnings.filterwarnings('ignore')											# ignore by default
from matplotlib.ticker import LinearLocator										# graphs
pd.set_option('display.max_columns', None)										# show all columns
pd.set_option('display.max_rows', 2000)											# show all rows
np.set_printoptions(threshold=sys.maxsize)										# show arrays full
pd.set_option("display.max_colwidth", -1)										# show a complete text in a cell
from xlsxwriter.workbook import Workbook										# CSV writing
import csv														# CSV writing	
import xgboost as xgb													# prediction
import pickle														# prediction	
import sklearn														# mutual information
import statsmodels.api as sm												# coefficient
from sklearn.ensemble import RandomForestClassifier									# random forest
from sklearn import linear_model											# linear regression
import pymysql														# MySql connection
import datetime														# time conversions
import random	
import glob

In [515]:
# Brazil and Mexico, August and September only, Rank below 50, Product analysis
all_files = glob.glob(r'C:\Users\milad\Desktop' + "/*.csv")
li = []
for filename in all_files:
    df = pd.read_csv(filename, sep='|')
    df['Category'] = np.nan
    df['Category'][:df.shape[0]] = filename
    li.append(df)
df = pd.concat(li, axis=0, ignore_index=True)

In [516]:
df.drop(columns=['Unnamed: 0','Authors/Company','Edition/Console','Max_prices'], inplace=True)
df = df.drop_duplicates(subset=['Rank', 'Product Names', 'Stars', 'Reviews','Price_std_or_min', 'Category'], keep='first')
df['time'] = pd.to_datetime(df['time'])
df = df.sort_values(['Product Names', 'time'], ascending=[True, True])
df = df.reset_index(drop=True)
df.columns = ['Date', 'Rank', 'Product', 'Score','ReviewsNum','Price','Category']
df = df.dropna(how='all')
df.drop(df.loc[(df['Date'] < '2020-08-01') | (df['Date'] > '2020-09-30')].index, inplace=True)
df.drop(df.loc[df['Product'].isnull()].index, inplace=True)
allnulls = df.loc[(((df['Rank'].isnull()) & (df['Score'].isnull())) & (df['ReviewsNum'].isnull())) & (df['Price'].isnull())]
df.drop(allnulls.index, inplace=True)
df.replace({'Product': {'  ': ' '}}, inplace=True, regex=True)
df = df.drop_duplicates(subset=['Rank', 'Product', 'Score', 'ReviewsNum','Price','Category'], keep='first')
df['Price'] = df['Price'].round(0)
df.at[df.loc[df['Price'] == 0].index,'Price'] = np.nan
df.replace({'Category': {r'C:\\Users\\milad\\Desktop\\mx-': '', '.csv': '', 'and':'&','-':' '}}, inplace=True, regex=True)
df['Category'] = df['Category'].str.title()

In [517]:
index=0
for product in df['Product'].unique():
    test = df.loc[df['Product'] == product].reset_index(drop=True)
    standard1 = [0] * (test.shape[0]-1)
    standard2 = [0] * (test.shape[0]-1)
    for i in range(0,test.shape[0]-1):
        standard1[i] = test['ReviewsNum'][i+1] - test['ReviewsNum'][i]
        standard2[i] = test['Price'][i+1] - test['Price'][i]
    if np.nanstd(standard1) >= 100 or np.nanstd(standard2) >= 1500:
        print('Review STD1:',np.nanstd(standard1),'      Price STD2:',np.nanstd(standard2))
        display(df.loc[df['Product'] == product])
        print('---------------------------------------------------','\n')

Review STD1: 109.66239100074374       Price STD2: 0.0


Date  Rank                  Product  Score  ReviewsNum  \
1070 2020-08-06 15:26:00  40.0  10,000 Days [Importado]  4.8    1057.0       
1071 2020-08-11 14:59:00  37.0  10,000 Days [Importado]  4.8    1057.0       
1072 2020-08-12 18:23:00  26.0  10,000 Days [Importado]  4.8    1057.0       
1073 2020-08-12 21:02:00  44.0  10,000 Days [Importado]  4.8    1057.0       
1074 2020-09-09 20:08:00  19.0  10,000 Days [Importado]  4.8    1336.0       
1075 2020-09-10 17:31:00  21.0  10,000 Days [Importado]  4.8    1359.0       

      Price Category  
1070  322.0  Music    
1071  322.0  Music    
1072  322.0  Music    
1073  322.0  Music    
1074  322.0  Music    
1075  322.0  Music

--------------------------------------------------- 

Review STD1: 211.34123970196973       Price STD2: 16.697471531808503


Date  Rank         Product  Score  ReviewsNum  Price  \
1901 2020-08-05 14:46:00  37.0  1917 [Blu-ray]  4.5    423.0       428.0   
1902 2020-08-05 15:32:00  37.0  1917 [Blu-ray]  4.5    423.0       429.0   
1903 2020-08-27 23:05:00  41.0  1917 [Blu-ray]  4.6    937.0       415.0   
1904 2020-09-08 15:56:00  21.0  1917 [Blu-ray]  4.7    2131.0      314.0   
1905 2020-09-08 16:46:00  21.0  1917 [Blu-ray]  4.7    2135.0      314.0   
1906 2020-09-08 17:36:00  21.0  1917 [Blu-ray]  4.7    2147.0      314.0   
1907 2020-09-09 12:34:00  26.0  1917 [Blu-ray]  4.7    2260.0      314.0   
1908 2020-09-09 20:08:00  19.0  1917 [Blu-ray]  4.7    2309.0      314.0   
1909 2020-09-10 14:19:00  14.0  1917 [Blu-ray]  4.7    2406.0      314.0   
1910 2020-09-10 15:09:00  14.0  1917 [Blu-ray]  4.7    2409.0      314.0   
1911 2020-09-10 15:59:00  14.0  1917 [Blu-ray]  4.7    2412.0      314.0   
1912 2020-09-10 16:49:00  14.0  1917 [Blu-ray]  4.7    2416.0      314.0   
1913 2020-09-10 17:31:00  23.0  1917 [Blu-ray]  4.7    2416.0      314.0   
1914 2020-09-11 15:43:00  9.0   1917 [Blu-ray]  4.7    2567.0      314.0   
1915 2020-09-11 17:26:00  17.0  1917 [Blu-ray]  4.7    2567.0      314.0   
1916 2020-09-11 19:57:00  7.0   1917 [Blu-ray]  4.7    2567.0      314.0   
1917 2020-09-11 20:48:00  7.0   1917 [Blu-ray]  4.7    2572.0      314.0   
1918 2020-09-11 21:38:00  7.0   1917 [Blu-ray]  4.7    2579.0      314.0   
1919 2020-09-11 22:29:00  10.0  1917 [Blu-ray]  4.7    2579.0      314.0   
1920 2020-09-12 01:01:00  19.0  1917 [Blu-ray]  4.7    2579.0      314.0   
1921 2020-09-12 14:03:00  29.0  1917 [Blu-ray]  4.7    2641.0      314.0   
1922 2020-09-12 20:48:00  22.0  1917 [Blu-ray]  4.7    2677.0      314.0   
1923 2020-09-12 21:39:00  22.0  1917 [Blu-ray]  4.7    2682.0      314.0   
1924 2020-09-12 23:20:00  41.0  1917 [Blu-ray]  4.7    2682.0      314.0   
1925 2020-09-15 19:22:00  33.0  1917 [Blu-ray]  4.7    2908.0      314.0   
1926 2020-09-15 21:54:00  12.0  1917 [Blu-ray]  4.7    2908.0      314.0   
1927 2020-09-16 01:16:00  23.0  1917 [Blu-ray]  4.7    2908.0      314.0   
1928 2020-09-16 02:06:00  23.0  1917 [Blu-ray]  4.7    2909.0      314.0   
1929 2020-09-16 18:52:00  25.0  1917 [Blu-ray]  4.7    2943.0      314.0   
1930 2020-09-16 22:43:00  38.0  1917 [Blu-ray]  4.7    2943.0      314.0   
1931 2020-09-17 00:24:00  14.0  1917 [Blu-ray]  4.7    2943.0      314.0   
1932 2020-09-17 12:42:00  37.0  1917 [Blu-ray]  4.7    2973.0      314.0   
1933 2020-09-18 20:47:00  46.0  1917 [Blu-ray]  4.7    3007.0      314.0   
1934 2020-09-19 13:45:00  23.0  1917 [Blu-ray]  4.7    3038.0      314.0   
1935 2020-09-19 15:28:00  45.0  1917 [Blu-ray]  4.7    3038.0      314.0   
1936 2020-09-19 23:41:00  34.0  1917 [Blu-ray]  4.7    3038.0      314.0   
1937 2020-09-20 02:14:00  50.0  1917 [Blu-ray]  4.7    3038.0      314.0   

     Category  
1901  Dvd      
1902  Dvd      
1903  Dvd      
1904  Dvd      
1905  Dvd      
1906  Dvd      
1907  Dvd      
1908  Dvd      
1909  Dvd      
1910  Dvd      
1911  Dvd      
1912  Dvd      
1913  Dvd      
1914  Dvd      
1915  Dvd      
1916  Dvd      
1917  Dvd      
1918  Dvd      
1919  Dvd      
1920  Dvd      
1921  Dvd      
1922  Dvd      
1923  Dvd      
1924  Dvd      
1925  Dvd      
1926  Dvd      
1927  Dvd      
1928  Dvd      
1929  Dvd      
1930  Dvd      
1931  Dvd      
1932  Dvd      
1933  Dvd      
1934  Dvd      
1935  Dvd      
1936  Dvd      
1937  Dvd

--------------------------------------------------- 

Review STD1: 239.38405653264584       Price STD2: 41.940128266069465


...

Date  Rank  \
113031 2020-08-01 17:57:00  7.0    
113032 2020-08-01 18:12:00  7.0    
113033 2020-08-02 20:12:00  5.0    
113034 2020-08-02 20:25:00  5.0    
113035 2020-08-02 20:37:00  5.0    
113036 2020-08-03 13:45:00  7.0    
113037 2020-08-03 15:10:00  7.0    
113038 2020-08-03 22:13:00  40.0   
113039 2020-08-04 10:30:00  35.0   
113040 2020-08-04 14:29:00  46.0   
113041 2020-08-05 11:44:00  46.0   
113042 2020-08-05 12:55:00  46.0   
113043 2020-08-05 14:46:00  47.0   
113044 2020-08-05 15:09:00  47.0   
113045 2020-09-15 22:44:00  36.0   
113046 2020-09-16 01:15:00  15.0   
113047 2020-09-16 14:38:00  8.0    
113048 2020-09-16 16:20:00  9.0    
113049 2020-09-17 00:23:00  7.0    
113050 2020-09-17 12:41:00  7.0    
113051 2020-09-17 14:23:00  5.0    
113052 2020-09-17 19:07:00  6.0    
113053 2020-09-18 12:02:00  6.0    
113054 2020-09-18 14:36:00  10.0   
113055 2020-09-19 13:44:00  9.0    
113056 2020-09-19 15:28:00  8.0    
113057 2020-09-19 21:07:00  10.0   
113058 2020-09-19 23:40:00  12.0   
113059 2020-09-20 12:20:00  13.0   
113060 2020-09-20 13:11:00  14.0   
113061 2020-09-20 19:08:00  15.0   
113062 2020-09-21 10:52:00  12.0   
113063 2020-09-21 11:44:00  13.0   
113064 2020-09-21 14:18:00  11.0   
113065 2020-09-21 20:15:00  14.0   
113066 2020-09-22 12:33:00  11.0   
113067 2020-09-22 21:04:00  13.0   
113068 2020-09-22 21:55:00  13.0   
113069 2020-09-23 12:09:00  10.0   
113070 2020-09-23 13:51:00  9.0    
113071 2020-09-23 19:50:00  14.0   
113072 2020-09-24 11:44:00  30.0   
113073 2020-09-24 12:36:00  21.0   
113074 2020-09-24 16:03:00  25.0   
113075 2020-09-24 16:54:00  25.0   
113076 2020-09-24 21:25:00  41.0   

                                                                 Product  \
113031  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113032  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113033  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113034  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113035  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113036  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113037  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113038  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113039  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113040  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113041  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113042  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113043  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113044  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113045  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113046  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113047  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113048  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113049  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113050  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113051  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113052  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113053  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113054  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113055  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113056  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113057  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113058  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113059  Funko Pop! Movies: John Wick - John in Black Suit with Dog Buddy   
113060  Funko Pop! Movies: John Wick - John in Bl

--------------------------------------------------- 

Review STD1: 116.71559712499824       Price STD2: 75.02380574571933


Date  Rank  \
113085 2020-08-24 13:09:00  43.0   
113086 2020-08-25 16:20:00  41.0   
113087 2020-08-25 22:27:00  33.0   
113088 2020-08-25 23:18:00  33.0   
113089 2020-08-26 11:35:00  43.0   
113090 2020-08-26 13:13:00  43.0   
113091 2020-08-26 14:01:00  43.0   
113092 2020-09-15 13:27:00  42.0   

                                                                                                   Product  \
113085  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113086  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113087  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113088  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113089  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113090  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113091  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   
113092  Funko Pop! TV - Dinosaurs Figurina de Colección Baby Sinclair, 10", Color Multicolor, Paquete de 1   

        Score  ReviewsNum  Price Category  
113085  4.8    214.0       259.0  Toys     
113086  4.8    225.0       259.0  Toys     
113087  4.8    225.0       259.0  Toys     
113088  4.8    225.0       399.0  Toys     
113089  4.8    240.0       389.0  Toys     
113090  4.8    243.0       389.0  Toys     
113091  4.8    243.0       399.0  Toys     
113092  4.8    581.0       259.0  Toys

--------------------------------------------------- 



KeyboardInterrupt: 

In [518]:
df.drop(df.loc[df['Product'] == '1984'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Abbey Road Anniversary (1LP)'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Audífonos Gamer con Micrófono para PS4 Xbox One PC, Diadema Auriculares Alámbrico Estéreo para Juegos Cancelación de…'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'BR - GAME OF THRONES STEELBOOK S.8 [Blu-ray'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Bosch DDMS20 - Juego de Atornillado y Taladrado Impact Tough, Maletín Personalizable, 20 piezas'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Bosch MS4041 - Juego mixto de brocas y puntas de atornillado de 41 piezas'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Champion - Playera clásica de Manga Corta para Hombre'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Chromatica (Vinyl)'].index , inplace=True)
df.drop(df.loc[df['Product'] == 'Chronicle: The 20 Greatest Hits (Vinyl) [Importado]'].index , inplace=True)

In [520]:
dfresult = pd.DataFrame(data={'Country':[''],'Category':[''],'Product':[''],'Rank':[''] ,'Rank+/-':[''],'Score':[''],
        'ImproveRate':[''],'ReviewsMax':[''],'Popularity':[''],'TrustIndex':[''],'Price':[''],'Profitability(K)':[''],'PriceVolatility':['']},
columns=['Country','Category','Product','Rank','Rank+/-','Score','ImproveRate','ReviewsMax','Popularity','TrustIndex','Price',
        'Profitability(K)','PriceVolatility'])

index=0
for Product in df['Product'].unique():
    Indicator = df.loc[df['Product'] == Product]
    dfresult.at[index, 'Country'] = 'Mexico'
    dfresult.at[index, 'Category'] = Indicator.head(1)['Category'].sum()
    dfresult.at[index, 'Product'] = Product
    dfresult.at[index, 'Rank'] = math.ceil(Indicator['Rank'].median())
    dfresult.at[index, 'Rank+/-'] = (Indicator.tail(1)['Rank'].sum()) - (Indicator.head(1)['Rank'].sum())
    dfresult.at[index, 'Score'] = round(Indicator['Score'].mean(),1)
    
    if Indicator['Score'].notnull().sum() == 0:
        dfresult.at[index, 'ImproveRate'] = np.nan
    else:
        dfresult.at[index, 'ImproveRate'] = ((Indicator.tail(1)['Score'].sum()) - (Indicator.loc[Indicator['Score'].notnull()].head(1)['Score'].sum()))*(Indicator.tail(1)['ReviewsNum'].sum())
        
    dfresult.at[index, 'ReviewsMax'] = Indicator['ReviewsNum'].max()
    
    opt = df.loc[(df['Product'] == Product) & (df['ReviewsNum'].notnull())]
    dfresult.at[index, 'Popularity'] = round(((opt['ReviewsNum'].tail(1).sum())-(opt['ReviewsNum'].head(1).sum()))/((((opt['Date'].tail(1).reset_index()) - (opt['Date'].head(1).reset_index()))['Date']/np.timedelta64(1, 'D')).sum()),1)
    
    dfresult.at[index, 'TrustIndex'] = round(((Indicator['Score'].mean())/(Indicator['Rank'].median()))*(Indicator.tail(1)['ReviewsNum'].sum()),1)
    
    if Indicator['Price'].notnull().sum() == 0:
        dfresult.at[index, 'Price'] = np.nan
        dfresult.at[index, 'Profitability(K)'] = np.nan
    else:
        dfresult.at[index, 'Price'] = Indicator['Price'].mode().sum()
        dfresult.at[index, 'Profitability(K)'] = round(((Indicator['ReviewsNum'].max()-Indicator['ReviewsNum'].min())*(Indicator['Price'].mode().sum()))/1000,1)
    
    dfresult.at[index, 'PriceVolatility'] = round(Indicator['Price'].std(),1)

    index = index + 1
dfresult = dfresult.sort_values(['TrustIndex'], ascending=[False])
dfresult

Country        Category  \
3158   Mexico  Amazon Devices   
2367   Mexico  Videogames       
10748  Mexico  Sports           
9438   Mexico  Electronics      
2364   Mexico  Videogames       
...       ...         ...       
10974  Mexico  H&Made           
10983  Mexico  H&Made           
10984  Mexico  H&Made           
10991  Mexico  Music            
11002  Mexico  Digital Text     

                                                                                                                       Product  \
3158   Echo Dot (3ra generación) - Bocina inteligente con Alexa - Granate                                                        
2367   Control Inalámbrico Xbox One - Standard Edition - Black Elite 2                                                           
10748  Xiaomi Mi Band 4                                                                                                          
9438   TP-LINK TL-WA850RE Repetidor de Wifi Extensor de Cobertura Inalámbrico Universal, 300Mbps, Enchufe de Pared, Tipo Plug…   
2364   Control Inalámbrico Xbox One - Special Edition - Blue                                                                     
...                                                      ...                                                                     
10974  smash cake PLIM PLIM                                                                                                      
10983  vestido PLIM PLIM                                                                                                         
10984  vestido PLIM PLIM talloa 4                                                                                                
10991  ¡¡¡VA POR MEXICO!!!                                                                                                       
11002  Éxito a través del dolor: Como afrontar la discapacidad de un hijo.                                                       

      Rank Rank+/- Score ImproveRate ReviewsMax Popularity TrustIndex Price  \
3158   1    1       4.8   0           37593      171.3      180422     849    
2367   5    18      4.7   0           70752      808.7      66506.9    4299   
10748  3   -10      4.7   6754        33771      241.1      52691.1    534    
9438   3   -3       4.5   0           33935      135.5      50895      449    
2364   6   -5       4.7   0           60500      152.2      47391.7    1349   
...   ..   ..       ...  ..             ...        ...          ...     ...   
10974  42   0       NaN   NaN         NaN        NaN        NaN        535    
10983  50   0       NaN   NaN         NaN        NaN        NaN        515    
10984  48   0       NaN   NaN         NaN        NaN        NaN        515    
10991  37   4       NaN   NaN         NaN        NaN        NaN        173    
11002  14   38      NaN   NaN         NaN        NaN        NaN        21     

      Profitability(K) PriceVolatility  
3158   8600.4           47.7            
2367   35509.7          0               
10748  7617.5           40              
9438   10600            41.1            
2364   3120.2           91.8            
...       ...            ...            
10974  NaN              NaN             
10983  NaN              NaN             
10984  NaN              NaN             
10991  NaN              0               
11002  NaN              0               

[11006 rows x 13 columns]

In [521]:
dfresult.to_csv('Mexico.csv', index=None)

In [522]:
df1 = pd.read_csv('Brazil.csv')
df2 = pd.read_csv('Mexico.csv')
df = df1.append(df2, ignore_index=True)
df = df.sort_values(['TrustIndex'], ascending=[False])
df = df.reset_index(drop=True)
df.head(1000)

Country             Category  \
0    Brazil  Mobile Apps           
1    Mexico  Amazon Devices        
2    Brazil  Amazon Devices        
3    Brazil  Sports                
4    Mexico  Videogames            
5    Brazil  Amazon Devices        
6    Mexico  Sports                
7    Mexico  Electronics           
8    Mexico  Videogames            
9    Mexico  Automotive            
10   Mexico  Electronics           
11   Brazil  Computers             
12   Brazil  Amazon Devices        
13   Mexico  Electronics           
14   Mexico  Electronics           
15   Brazil  Toys                  
16   Mexico  Amazon Devices        
17   Mexico  Kitchen               
18   Brazil  Videogames            
19   Mexico  Kitchen               
20   Mexico  Kitchen               
21   Mexico  Hpc                   
22   Mexico  Electronics           
23   Brazil  Videogames            
24   Brazil  Home                  
25   Mexico  Videogames            
26   Brazil  Office                
27   Mexico  Videogames            
28   Mexico  Shoes                 
29   Mexico  Kitchen               
30   Mexico  Videogames            
31   Mexico  Videogames            
32   Mexico  Videogames            
33   Brazil  Music                 
34   Brazil  Fashion               
35   Mexico  Electronics           
36   Brazil  Computers             
37   Brazil  Electronics           
38   Mexico  Grocery               
39   Brazil  Toys                  
40   Mexico  Electronics           
41   Brazil  Baby Products         
42   Mexico  Videogames            
43   Mexico  Videogames            
44   Mexico  Videogames            
45   Mexico  Officeproduct         
46   Mexico  Pet Supplies          
47   Mexico  Musical Instruments   
48   Mexico  Videogames            
49   Mexico  Toys                  
50   Mexico  Videogames            
51   Mexico  Baby                  
52   Mexico  Pet Supplies          
53   Brazil  Baby Products         
54   Mexico  Grocery               
55   Mexico  Kitchen               
56   Brazil  Books                 
57   Mexico  Shoes                 
58   Mexico  Musical Instruments   
59   Mexico  Toys                  
60   Mexico  Pet Supplies          
61   Mexico  Tools                 
62   Mexico  Electronics           
63   Mexico  Toys                  
64   Mexico  Pet Supplies          
65   Mexico  Kitchen               
66   Mexico  Kitchen               
67   Brazil  Fashion               
68   Mexico  Kitchen               
69   Mexico  Pet Supplies          
70   Mexico  Toys                  
71   Mexico  Electronics           
72   Mexico  Baby                  
73   Mexico  Officeproduct         
74   Mexico  Musical Instruments   
75   Mexico  Kitchen               
76   Mexico  Kitchen               
77   Mexico  Videogames            
78   Mexico  Officeproduct         
79   Mexico  Shoes                 
80   Mexico  Pet Supplies          
81   Mexico  Shoes                 
82   Mexico  Amazon Devices        
83   Brazil  Amazon Devices        
84   Mexico  Sports                
85   Brazil  Home                  
86   Brazil  Computers             
87   Brazil  Home                  
88   Mexico  Electronics           
89   Mexico  Sports                
90   Mexico  Videogames            
91   Mexico  Pet Supplies          
92   Mexico  Toys                  
93   Mexico  Toys                  
94   Brazil  Electronics           
95   Mexico  Officeproduct         
96   Mexico  Officeproduct         
97   Mexico  Kitchen               
98   Mexico  Electronics           
99   Brazil  Baby Products         
100  Mexico  Sports                
101  Brazil  Home                  
102  Mexico  Officeproduct         
103  Mexico  Kitchen               
104  Mexico  Kitchen               
105  Mexico  Pet Supplies          
106  Brazil  Computers             
107  Mexico  Kitchen               
108  Brazil  Digital Text          
109  Mexico  Musical Instruments   
110  Mex

In [531]:
# Mexico yielded more profit in Sep and Aug

df.loc[df['Profitability(K)'] > 100]['Country'].value_counts()

Mexico    1306
Brazil    160 
Name: Country, dtype: int64

In [544]:
# Investing in the following cats

df.loc[df['Profitability(K)'] > 1000]['Category'].value_counts().loc[lambda x : x>20]

Videogames             53
Electronics            46
Musical Instruments    24
Shoes                  22
Name: Category, dtype: int64

In [550]:
# In which cats people have low trust in eCommerce platform?

df.loc[(df['TrustIndex'] < 1) & (df['TrustIndex'].notnull())]['Category'].value_counts().loc[lambda x : x>500]

H&Made        684
Automotive    531
Name: Category, dtype: int64

In [551]:
# Growing Market:

df.loc[df['ImproveRate'] > 0]['Country'].value_counts()

Brazil    1411
Mexico    1357
Name: Country, dtype: int64

In [560]:
# Market Price Stability,considering inflation more than 1% per month:

df.loc[(df['PriceVolatility'] > 2) & (df['PriceVolatility'] < 200)]['Country'].value_counts()

Mexico    3618
Brazil    3480
Name: Country, dtype: int64